In [1]:
from mmpose.datasets import build_dataloader, build_dataset
from mmcv import Config
from mmpose.models import build_posenet
from mmcv.runner import get_dist_info, init_dist, load_checkpoint
import mmcv
from mmcv.parallel import MMDataParallel
from mmpose.apis import multi_gpu_test, single_gpu_test

In [2]:
config_file = '/mnt/ssd/marley/ID_Card/mmpose/configs/ID_card/overfit_higherhrnet_w32_IDCard_512x512.py'
cfg = Config.fromfile(config_file)

In [3]:
cfg.model.pretrained = None
cfg.data.test.test_mode = True

In [4]:
# build the dataloader
dataset = build_dataset(cfg.data.test, dict(test_mode=True))
dataloader_setting = dict(
    samples_per_gpu=12,
    workers_per_gpu=cfg.data.get('workers_per_gpu', 1),
    dist=False,
    shuffle=False,
    drop_last=False)
dataloader_setting = dict(dataloader_setting,
                              **cfg.data.get('test_dataloader', {}))
data_loader = build_dataloader(dataset, **dataloader_setting)

loading annotations into memory...
Done (t=0.06s)
creating index...
index created!
=> num_images: 3400


In [5]:
# build the model and load checkpoint
checkpoint='/mnt/ssd/marley/ID_Card/mmpose/work_dirs/overfit_higherhrnet_w32_IDCard_512x512/latest.pth'
model = build_posenet(cfg.model)
load_checkpoint(model, checkpoint, map_location='cpu')

Use load_from_local loader


{'meta': {'mmpose_version': '0.18.0464c933',
  'config': "dataset_info = dict(\n    dataset_name='ID_card',\n    paper_info=dict(\n        author='Marley (Nhi Ngo)',\n        title='ID Card Crop and Alignment',\n        container='Techainer',\n        year='2021',\n        homepage='https://techainer.com/'),\n    keypoint_info=dict({\n        0:\n        dict(\n            name='top_left',\n            id=0,\n            color=[255, 0, 0],\n            type='upper',\n            swap='top_right'),\n        1:\n        dict(\n            name='bottom_left',\n            id=1,\n            color=[0, 255, 0],\n            type='lower',\n            swap='bottom_right'),\n        2:\n        dict(\n            name='bottom_right',\n            id=2,\n            color=[0, 255, 255],\n            type='lower',\n            swap='bottom_left'),\n        3:\n        dict(\n            name='top_right',\n            id=3,\n            color=[255, 255, 0],\n            type='upper',\n          

In [6]:
model = MMDataParallel(model, device_ids=[0])
outputs = single_gpu_test(model, data_loader)

[                                                  ] 0/3400, elapsed: 0s, ETA:

RuntimeError: Caught RuntimeError in DataLoader worker process 0.
Original Traceback (most recent call last):
  File "/mnt/ssd/marley/ID_Card/open-mmlab/lib/python3.6/site-packages/torch/utils/data/_utils/worker.py", line 287, in _worker_loop
    data = fetcher.fetch(index)
  File "/mnt/ssd/marley/ID_Card/open-mmlab/lib/python3.6/site-packages/torch/utils/data/_utils/fetch.py", line 47, in fetch
    return self.collate_fn(data)
  File "/mnt/ssd/marley/ID_Card/open-mmlab/lib/python3.6/site-packages/mmcv/parallel/collate.py", line 81, in collate
    for key in batch[0]
  File "/mnt/ssd/marley/ID_Card/open-mmlab/lib/python3.6/site-packages/mmcv/parallel/collate.py", line 81, in <dictcomp>
    for key in batch[0]
  File "/mnt/ssd/marley/ID_Card/open-mmlab/lib/python3.6/site-packages/mmcv/parallel/collate.py", line 84, in collate
    return default_collate(batch)
  File "/mnt/ssd/marley/ID_Card/open-mmlab/lib/python3.6/site-packages/torch/utils/data/_utils/collate.py", line 56, in default_c

In [ ]:
eval_config = cfg.get('evaluation', {})

In [ ]:
work_dir = '/mnt/ssd/marley/ID_Card/mmpose/work_dirs/overfit_higherhrnet_w32_IDCard_512x512'
results = dataset.evaluate(outputs, work_dir, **eval_config)

/mnt/ssd/marley/ID_Card/open-mmlab/lib/python3.6/site-packages/json_tricks/encoders.py:367: UserWarning: json-tricks: numpy scalar serialization is experimental and may work differently in future versions
  warnings.warn('json-tricks: numpy scalar serialization is experimental and may work differently in future versions')


Loading and preparing results...
DONE (t=0.03s)
creating index...
index created!
Running per image evaluation...
Evaluate annotation type *keypoints*
DONE (t=1.59s).
Accumulating evaluation results...
DONE (t=0.10s).
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=   all | maxDets= 20 ] =  0.005
 Average Precision  (AP) @[ IoU=0.50      | area=   all | maxDets= 20 ] =  0.005
 Average Precision  (AP) @[ IoU=0.75      | area=   all | maxDets= 20 ] =  0.005
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=medium | maxDets= 20 ] = -1.000
 Average Precision  (AP) @[ IoU=0.50:0.95 | area= large | maxDets= 20 ] =  0.005
 Average Recall     (AR) @[ IoU=0.50:0.95 | area=   all | maxDets= 20 ] =  0.044
 Average Recall     (AR) @[ IoU=0.50      | area=   all | maxDets= 20 ] =  0.050
 Average Recall     (AR) @[ IoU=0.75      | area=   all | maxDets= 20 ] =  0.042
 Average Recall     (AR) @[ IoU=0.50:0.95 | area=medium | maxDets= 20 ] = -1.000
 Average Recall     (AR) @[ IoU=0.50:0.95 | area= larg